In [1]:
# disable warnings up front for a cleaner experience
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

# Geographic Data

Many applications focus on data as it pertains to actual geographic locations. Plotting visual locations on a realistic map gives the viewer a sense of scale and context otherwise not present. However, plotting geographic data is a very difficult technical task; there are a few considerations that need to be taken that plotting libraries try to abstract away from the developer (projections, tiles, geo-shapes, etc.).

We will use two new libraries:

* `geoviews` - a visualzation library built on top of `holoviews`, geographic mapping libraries, and data sources  
* `geopandas` - a pandas extensions built to handle geographic/shape data

These tools are not easy to use, but the results are quite powerful. Let's get some simple examples out of the way and begin with some imports.

In [2]:
import geopandas as gpd
import geoviews as gv
import holoviews as hv
import hvplot.pandas
import pandas as pd
import panel as pn
gv.extension('bokeh')
hv.extension('bokeh')
pn.extension()

Commonly we will use map tiles as the basis for our geographic visualizations. There are tons of community resources poured into developing and maintaining map tiles, and so there are also restrictions that exist around them (namely with respect to downloading/offline use). We can use `geoviews` to load [Open Street Map](https://www.openstreetmap.org/) map tiles of the world to give a detailed view of the world.

In [3]:
world = gv.tile_sources.OSM() # Open Street map
world.opts(
    height=480,
    width=640
)

:WMTS   [Longitude,Latitude]

Try zooming and panning! Note that, amazingly, as we zoom in and out the level of detail shown on the map changes! Find us on the map! This allows us to work with data at varying/many scales. Let's combine this map with some data!

Let's say we want to plot the straight-line path from Philadelphia International Airpoint (PHL) to Los Angeles International Airpoirt (LAX). To do this we need coordinates of these airports. This data was pulled from the [Bureau of Transportation Statistics](https://www.transtats.bts.gov/DL_SelectFields.aspx?gnoyr_VQ=FLL&QO_fu146_anzr=).

## Lots of diff views in Geoviews 
- Not every one of the tile sources.
- Some have a shallow zoom value

In [5]:
airports = pd.read_csv('notebooks/data/T_MASTER_CORD.csv').set_index('AIRPORT')
usa_airports = airports[airports['AIRPORT_COUNTRY_NAME'] == 'United States'].drop_duplicates(['DISPLAY_AIRPORT_NAME'])

phl = usa_airports.loc['PHL']
phl

DISPLAY_AIRPORT_NAME              Philadelphia International
DISPLAY_AIRPORT_CITY_NAME_FULL              Philadelphia, PA
AIRPORT_COUNTRY_NAME                           United States
LATITUDE                                           39.868056
LONGITUDE                                         -75.248611
Name: PHL, dtype: object

In [6]:
usa_airports

DISPLAY_AIRPORT_NAME DISPLAY_AIRPORT_CITY_NAME_FULL  \
AIRPORT                                                           
01A         Afognak Lake Airport               Afognak Lake, AK   
03A      Bear Creek Mining Strip           Granite Mountain, AK   
04A              Lik Mining Camp                        Lik, AK   
05A         Little Squaw Airport               Little Squaw, AK   
06A                 Kizhuyak Bay                   Kizhuyak, AK   
...                          ...                            ...   
ZXX                  Vista Field                  Kennewick, WA   
ZXY                  Blake Field                      Delta, CO   
ZXZ           Waterville Airport                 Waterville, WA   
ZZV         Zanesville Municipal                 Zanesville, OH   
ZZZ      Unknown Point in Alaska        Unknown Point in Alaska   

        AIRPORT_COUNTRY_NAME   LATITUDE   LONGITUDE  
AIRPORT                                              
01A            United States  58.109444 -152.906667  
03A            United States  65.548056 -161.071667  
04A            United States  68.083333 -163.166667  
05A            United States  67.570000 -148.183889  
06A            United States  57.745278 -152.882778  
...                      ...        ...         ...  
ZXX            United States  46.218333 -119.209444  
ZXY            United States  38.783333 -108.065278  
ZXZ            United States  47.654167 -120.054167  
ZZV            United States  39.942778  -81.892500  
ZZZ            United States        NaN         NaN  

[3523 rows x 5 columns]

In [7]:
lax = usa_airports.loc['LAX']
lax

DISPLAY_AIRPORT_NAME              Los Angeles International
DISPLAY_AIRPORT_CITY_NAME_FULL              Los Angeles, CA
AIRPORT_COUNTRY_NAME                          United States
LATITUDE                                            33.9425
LONGITUDE                                       -118.408056
Name: LAX, dtype: object

In [8]:
# create a list of coordinates
path = [
    [phl.LONGITUDE, phl.LATITUDE],
    [lax.LONGITUDE, lax.LATITUDE]
]

# pass list of points to gv.Points to create geographic points
points = gv.Points(path).opts(size=10, color='red')

# pass list of points **wrapped in a list** to create a geographic path
straight_line_path = gv.Path([path]).opts(color='red', line_width=2)
# path here is not only a list pof co ordinates, 
# we wrap in another set of square braces, sicne a list of values required

esri_world = gv.tile_sources.EsriImagery()

# overlay all of the elements with the world map
(esri_world * straight_line_path * points).opts(
    title='Straight-Line Path from PHL to LAX',
    height=480,
    width=640
)

:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Path.I   :Path   [Longitude,Latitude]
   .Points.I :Points   [x,y]

If we want to add more points (either just points, or as a path) this starts to get quite clunky. This is where `geopandas` comes into play! `geopandas` is optimized for handling geographic data and geometries, so let's convert our `DataFrame` into a `GeoDataFrame`

In [9]:
# take some approximations for the bounding box around the continental USA
continental_usa_lon = [-124.736342, -66.945392]
continental_usa_lat = [24.521208, 49.382808]

# apply mask to select airports within the continental USA
cusa_airports = usa_airports[
    usa_airports.LONGITUDE.between(*continental_usa_lon) &
    usa_airports.LATITUDE.between(*continental_usa_lat)
]

# convert to GeoDataFrame
geo_airports = gpd.GeoDataFrame(
    cusa_airports, geometry=gpd.points_from_xy(cusa_airports.LONGITUDE, cusa_airports.LATITUDE)
)
geo_airports
# standardized, geometric repr of data
# since standardized format, geoviews impl and interacts with directly

DISPLAY_AIRPORT_NAME DISPLAY_AIRPORT_CITY_NAME_FULL  \
AIRPORT                                                                         
1B1                            Columbia County                     Hudson, NY   
1CA                        Rio Vista Municipal                  Rio Vista, CA   
1FL              NASA Shuttle Landing Facility                 Titusville, FL   
1FL      Space Florida Launch Landing Facility                 Titusville, FL   
1G4                          Grand Canyon West              Peach Springs, AZ   
...                                        ...                            ...   
ZXW                                    Skypark                   Paradise, CA   
ZXX                                Vista Field                  Kennewick, WA   
ZXY                                Blake Field                      Delta, CO   
ZXZ                         Waterville Airport                 Waterville, WA   
ZZV                       Zanesville Municipal                 Zanesville, OH   

        AIRPORT_COUNTRY_NAME   LATITUDE   LONGITUDE  \
AIRPORT                                               
1B1            United States  42.288889  -73.710278   
1CA            United States  38.193333 -121.703611   
1FL            United States  28.615000  -80.694444   
1FL            United States  28.615000  -80.694444   
1G4            United States  35.986111 -113.816944   
...                      ...        ...         ...   
ZXW            United States  39.709722 -121.615278   
ZXX            United States  46.218333 -119.209444   
ZXY            United States  38.783333 -108.065278   
ZXZ            United States  47.654167 -120.054167   
ZZV            United States  39.942778  -81.892500   

                            geometry  
AIRPORT                               
1B1       POINT (-73.71028 42.28889)  
1CA      POINT (-121.70361 38.19333)  
1FL       POINT (-80.69444 28.61500)  
1FL       POINT (-80.69444 28.61500)  
1G4      POINT (-113.81694 35.98611)  
...                              ...  
ZXW      POINT (-121.61528 39.70972)  
ZXX      POINT (-119.20944 46.21833)  
ZXY      POINT (-108.06528 38.78333)  
ZXZ      POINT (-120.05417 47.65417)  
ZZV       POINT (-81.89250 39.94278)  

[2736 rows x 6 columns]

This is largely the same, but now our dataframe also has a `geometry` column; this column contains [`shapefile`](https://en.wikipedia.org/wiki/Shapefile) geometry definitions, which we can use directly with `geoviews`!  

In [10]:
# scatter all airports
scatter_airports = gv.Points(geo_airports)
# interact between geoviews and geometry column is automatic when using geopandas

# create a slider for controlling marker size
marker_size_slider = pn.widgets.IntSlider(name='Marker Size', start=5, end=10, step=1)

# create dynamic function for 
@pn.depends(marker_size=marker_size_slider)
def plot_all_airports(marker_size):
    return (esri_world * scatter_airports.opts(
        size=marker_size,
        color='yellow',
        line_color='black',
        alpha=0.75,
        tools=['hover']
    )).opts(
        title='Continental USA Airports',
        height=480,
        width=640
    )

pn.Column(
    marker_size_slider,
    hv.DynamicMap(plot_all_airports)
)


BokehModel(combine_events=True, render_bundle={'docs_json': {'f6d13010-dae1-4066-8a9d-354e9f6674e2': {'version…

## Exercise

Find tour information (locations) for a band/artist that you like, and plot the path of their tour. We can use `geopy` to help us get lat/lon pairs for cities by name. We have some data found and ready in `data/abr_20th_ann_tour.dat`

In [11]:
# if we want to get geodedic locations based on city names, we can use geopy, but we need to install it.
import sys
%conda install -c conda-forge --yes --prefix {sys.prefix} geopy

# once installed we can use it like so:
# geolocator = Nominatim(user_agent="MyApp")
# location = geolocator.geocode("Philadelphia, PA")
# lat, lon = location.latitude, location.longitude

Retrieving notices: ...working... done
Channels:
 - conda-forge
 - defaults
Platform: osx-arm64
Solving environment: done

# All requested packages already installed.


Note: you may need to restart the kernel to use updated packages.


In [15]:
# read the raw data
# sample = []
with open('notebooks/data/abr_20th_ann_tour.dat', 'r', encoding = 'utf-8') as data_handle:
    # for data in data_handle:
    #     sample.append(data.strip().split(' - '))
    tour = data_handle.read()
print(tour)
# print(sample)

Feb. 15 - Silver Spring, MD - The Fillmore Silver Spring
Feb. 16 - Raleigh, NC - The Ritz
Feb. 17 - Atlanta, GA - Heaven at The Masquerade
Feb. 18 - Orlando, FL - Hear
Feb. 20 - Fort Lauderdale, FL - Revolution Live
Feb. 21 - Pensacola, FL - Vinyl Music Hall
Feb. 23 - Houston, TX - House of Blues
Feb. 24 - Dallas, TX - South Side Ballroom
Feb. 25 - San Antonio, TX - Vibes Event Center
Feb. 27 - Tempe, AZ - The Marquee
Feb. 28 - San Diego, CA - Soma
Mar. 01 - Anaheim, CA - House of Blues
Mar. 02 - Sacramento, CA - Ace Of Spades
Mar. 04 - Portland, OR - Roseland Theater
Mar. 05 - Seattle, WA - Showbox Sodo
Mar. 07 - Salt Lake City, UT - The Complex
Mar. 08 - Las Vegas, NV - House of Blues
Mar. 10 - Denver, CO - Fillmore Auditorium
Mar. 12 - Little Rock, AR - The Hall
Mar. 13 - Nashville, TN - Marathon Music Works
Mar. 14 - Charlotte, NC - The Fillmore Charlotte
Apr. 13 - Philadelphia, PA - The Fillmore Philadelphia
Apr. 14 - New York, NY - Palladium Times Square
Apr. 15 - Albany, NY - Em

In [16]:
# prep the data, throw into a dataframe
tour_data = [ line.split(' - ') for line in tour.split('\n')]
tour_df = pd.DataFrame(tour_data, columns = ['Date', 'City', 'Venue'])
tour_df

Date                    City                       Venue
0   Feb. 15       Silver Spring, MD  The Fillmore Silver Spring
1   Feb. 16             Raleigh, NC                    The Ritz
2   Feb. 17             Atlanta, GA    Heaven at The Masquerade
3   Feb. 18             Orlando, FL                        Hear
4   Feb. 20     Fort Lauderdale, FL             Revolution Live
5   Feb. 21           Pensacola, FL            Vinyl Music Hall
6   Feb. 23             Houston, TX              House of Blues
7   Feb. 24              Dallas, TX         South Side Ballroom
8   Feb. 25         San Antonio, TX          Vibes Event Center
9   Feb. 27               Tempe, AZ                 The Marquee
10  Feb. 28           San Diego, CA                        Soma
11  Mar. 01             Anaheim, CA              House of Blues
12  Mar. 02          Sacramento, CA               Ace Of Spades
13  Mar. 04            Portland, OR            Roseland Theater
14  Mar. 05             Seattle, WA                Showbox Sodo
15  Mar. 07      Salt Lake City, UT                 The Complex
16  Mar. 08           Las Vegas, NV              House of Blues
17  Mar. 10              Denver, CO         Fillmore Auditorium
18  Mar. 12         Little Rock, AR                    The Hall
19  Mar. 13           Nashville, TN        Marathon Music Works
20  Mar. 14           Charlotte, NC      The Fillmore Charlotte
21  Apr. 13        Philadelphia, PA   The Fillmore Philadelphia
22  Apr. 14            New York, NY      Palladium Times Square
23  Apr. 15              Albany, NY                 Empire Live
24  Apr. 16           Worcester, MA               The Palladium
25  Apr. 18       Niagara Falls, NY              Rapids Theater
26  Apr. 19           Royal Oak, MI     Royal Oak Music Theatre
27  Apr. 21        Grand Rapids, MI            The Intersection
28  Apr. 22           St. Louis, MO                    Red Flag
29  Apr. 23         Kansas City, MO                  The Truman
30  Apr. 25       Oklahoma City, OK            Diamond Ballroom
31  Apr. 26               Omaha, NE                    Slowdown
32  Apr. 28         Minneapolis, MN    The Fillmore Minneapolis
33  Apr. 29             Chicago, IL          Concord Music Hall
34  Apr. 30          Cincinnati, OH                     Bogarts
35   May 02           Cleveland, OH              House of Blues
36   May 03          Pittsburgh, PA                    Stage AE
37   May 05  North Myrtle Beach, SC              House of Blues
38   May 06            Richmond, VA                The National
39   May 07          Sayreville, NJ           Starland Ballroom
40   May 09             Toronto, ON         Danforth Music Hall
41   May 11            Montreal, QC                      Mtelus
42   May 12              Quebec, QC           Theatre Capitoles

In [17]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="MyApp")

# define a function named get_location to get the lat/lon using geopy!
def get_location(row):
    location = geolocator.geocode(row.City)
    return location.latitude, location.longitude

tour_df[['Latitude','Longitude']] = tour_df.apply(get_location, axis=1, result_type = 'expand')
# we need to tell pandas that we are getting more than one column, here
# we need to expand the output into multiple column in our dataframe
tour_df

Date                    City                       Venue   Latitude  \
0   Feb. 15       Silver Spring, MD  The Fillmore Silver Spring  38.995946   
1   Feb. 16             Raleigh, NC                    The Ritz  35.780398   
2   Feb. 17             Atlanta, GA    Heaven at The Masquerade  33.748992   
3   Feb. 18             Orlando, FL                        Hear  28.542111   
4   Feb. 20     Fort Lauderdale, FL             Revolution Live  26.122308   
5   Feb. 21           Pensacola, FL            Vinyl Music Hall  30.421309   
6   Feb. 23             Houston, TX              House of Blues  29.758938   
7   Feb. 24              Dallas, TX         South Side Ballroom  32.776272   
8   Feb. 25         San Antonio, TX          Vibes Event Center  29.424600   
9   Feb. 27               Tempe, AZ                 The Marquee  33.425512   
10  Feb. 28           San Diego, CA                        Soma  32.717420   
11  Mar. 01             Anaheim, CA              House of Blues  33.834752   
12  Mar. 02          Sacramento, CA               Ace Of Spades  38.581061   
13  Mar. 04            Portland, OR            Roseland Theater  45.520247   
14  Mar. 05             Seattle, WA                Showbox Sodo  47.603832   
15  Mar. 07      Salt Lake City, UT                 The Complex  40.759620   
16  Mar. 08           Las Vegas, NV              House of Blues  36.167256   
17  Mar. 10              Denver, CO         Fillmore Auditorium  39.739236   
18  Mar. 12         Little Rock, AR                    The Hall  34.746507   
19  Mar. 13           Nashville, TN        Marathon Music Works  36.162277   
20  Mar. 14           Charlotte, NC      The Fillmore Charlotte  35.227209   
21  Apr. 13        Philadelphia, PA   The Fillmore Philadelphia  39.952724   
22  Apr. 14            New York, NY      Palladium Times Square  40.712728   
23  Apr. 15              Albany, NY                 Empire Live  42.651167   
24  Apr. 16           Worcester, MA               The Palladium  42.262562   
25  Apr. 18       Niagara Falls, NY              Rapids Theater  43.084360   
26  Apr. 19           Royal Oak, MI     Royal Oak Music Theatre  42.489480   
27  Apr. 21        Grand Rapids, MI            The Intersection  42.963242   
28  Apr. 22           St. Louis, MO                    Red Flag  38.628028   
29  Apr. 23         Kansas City, MO                  The Truman  39.100105   
30  Apr. 25       Oklahoma City, OK            Diamond Ballroom  35.472989   
31  Apr. 26               Omaha, NE                    Slowdown  41.258746   
32  Apr. 28         Minneapolis, MN    The Fillmore Minneapolis  44.977300   
33  Apr. 29             Chicago, IL          Concord Music Hall  41.875562   
34  Apr. 30          Cincinnati, OH                     Bogarts  39.101454   
35   May 02           Cleveland, OH              House of Blues  41.499657   
36   May 03          Pittsburgh, PA                    Stage AE  40.441694   
37   May 05  North Myrtle Beach, SC              House of Blues  33.827841   
38   May 06            Richmond, VA                The National  37.538509   
39   May 07          Sayreville, NJ           Starland Ballroom  40.463536   
40   May 09             Toronto, ON         Danforth Music Hall  43.653482   
41   May 11            Montreal, QC                      Mtelus  45.503182   
42   May 12              Quebec, QC           Theatre Capitoles  46.813743   

     Longitude  
0   -77.027623  
1   -78.639099  
2   -84.390264  
3   -81.379030  
4   -80.143379  
5   -87.216915  
6   -95.367697  
7   -96.796856  
8   -98.495141  
9  -111.940016  
10 -117.162773  
11 -117.911732  
12 -121.493895  
13 -122.674194  
14 -122.330062  
15 -111.886797  
16 -115.148516  
17 -104.984862  
18  -92.289627  
19  -86.774298  
20  -80.843083  
21  -75.163526  
22  -74.006015  
23  -73.754968  
24  -71.801888  
25  -79.061469  
26  -83.144649  
27  -85.667864  
28  -90.191015  
29  -94.578142  
30  -97.517054  
31  -95.938376  
32  -93.26546

In [ ]:
# convert to geopandas
geo_tour = gpd.GeoDataFrame(
    tour_df, geometry=gpd.points_from_xy(tour_df.Longitude, tour_df.Latitude)
)
geo_tour

Date                    City                       Venue   Latitude  \
0   Feb. 15       Silver Spring, MD  The Fillmore Silver Spring  38.995946   
1   Feb. 16             Raleigh, NC                    The Ritz  35.780398   
2   Feb. 17             Atlanta, GA    Heaven at The Masquerade  33.748992   
3   Feb. 18             Orlando, FL                        Hear  28.542111   
4   Feb. 20     Fort Lauderdale, FL             Revolution Live  26.122308   
5   Feb. 21           Pensacola, FL            Vinyl Music Hall  30.421309   
6   Feb. 23             Houston, TX              House of Blues  29.758938   
7   Feb. 24              Dallas, TX         South Side Ballroom  32.776272   
8   Feb. 25         San Antonio, TX          Vibes Event Center  29.424600   
9   Feb. 27               Tempe, AZ                 The Marquee  33.425512   
10  Feb. 28           San Diego, CA                        Soma  32.717420   
11  Mar. 01             Anaheim, CA              House of Blues  33.834752   
12  Mar. 02          Sacramento, CA               Ace Of Spades  38.581061   
13  Mar. 04            Portland, OR            Roseland Theater  45.520247   
14  Mar. 05             Seattle, WA                Showbox Sodo  47.603832   
15  Mar. 07      Salt Lake City, UT                 The Complex  40.759620   
16  Mar. 08           Las Vegas, NV              House of Blues  36.167256   
17  Mar. 10              Denver, CO         Fillmore Auditorium  39.739236   
18  Mar. 12         Little Rock, AR                    The Hall  34.746507   
19  Mar. 13           Nashville, TN        Marathon Music Works  36.162277   
20  Mar. 14           Charlotte, NC      The Fillmore Charlotte  35.227209   
21  Apr. 13        Philadelphia, PA   The Fillmore Philadelphia  39.952724   
22  Apr. 14            New York, NY      Palladium Times Square  40.712728   
23  Apr. 15              Albany, NY                 Empire Live  42.651167   
24  Apr. 16           Worcester, MA               The Palladium  42.262562   
25  Apr. 18       Niagara Falls, NY              Rapids Theater  43.084360   
26  Apr. 19           Royal Oak, MI     Royal Oak Music Theatre  42.489480   
27  Apr. 21        Grand Rapids, MI            The Intersection  42.963242   
28  Apr. 22           St. Louis, MO                    Red Flag  38.628028   
29  Apr. 23         Kansas City, MO                  The Truman  39.100105   
30  Apr. 25       Oklahoma City, OK            Diamond Ballroom  35.472989   
31  Apr. 26               Omaha, NE                    Slowdown  41.258746   
32  Apr. 28         Minneapolis, MN    The Fillmore Minneapolis  44.977300   
33  Apr. 29             Chicago, IL          Concord Music Hall  41.875562   
34  Apr. 30          Cincinnati, OH                     Bogarts  39.101454   
35   May 02           Cleveland, OH              House of Blues  41.499657   
36   May 03          Pittsburgh, PA                    Stage AE  40.441694   
37   May 05  North Myrtle Beach, SC              House of Blues  33.827841   
38   May 06            Richmond, VA                The National  37.538509   
39   May 07          Sayreville, NJ           Starland Ballroom  40.463536   
40   May 09             Toronto, ON         Danforth Music Hall  43.653482   
41   May 11            Montreal, QC                      Mtelus  45.503182   
42   May 12              Quebec, QC           Theatre Capitoles  46.813743   

     Longitude                     geometry  
0   -77.027623   POINT (-77.02762 38.99595)  
1   -78.639099   POINT (-78.63910 35.78040)  
2   -84.390264   POINT (-84.39026 33.74899)  
3   -81.379030   POINT (-81.37903 28.54211)  
4   -80.143379   POINT (-80.14338 26.12231)  
5   -87.216915   POINT (-87.21691 30.42131)  
6   -95.367697   POINT (-95.36770 29.75894)  
7   -96.796856   POINT (-96.79686 32.77627)  
8   -98.495141   POINT (-98.49514 29.42460)  
9  -111.940016  POINT (-111.94002 33.42551)  
10 -117.162773  POINT (-117.16277 32.71742)  
11 -117.911732  POINT 

In [ ]:
# plot path and stops over the world
world * gv.Points(geo_tour) * gv.Path([geo_tour])

:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Points.I :Points   [Longitude,Latitude]   (Date,City,Venue,Latitude,Longitude)
   .Path.I   :Path   [Longitude,Latitude]

In [ ]:
path = gv.Path([geo_tour]).opts(
    line_width=3,
    color = 'black'
)

stops = gv.Points(geo_tour).opts(
    color = 'Date',
    show_legend=False,
    size=10,
    tools = ['hover']
)
(world * path * stops).opts(
    title = 'August Burns Red - 20th Anniversary Tour',
    height = 480,
    width = 720
)


:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Path.I   :Path   [Longitude,Latitude]
   .Points.I :Points   [Longitude,Latitude]   (Date,City,Venue,Latitude,Longitude)

## Extra Credit
 - Find tourdate for other band, from raw, go through odata, prep, and getting to plot like this [geo plot]
 - submit by friday

Obviously plotting points and lines on top of a map is extremely useful, but we can go farther. We briefly glossed over the geometry column that `geopandas` created. The data stored in this column is a [`shapefile`](https://en.wikipedia.org/wiki/Shapefile) format. We cna load shapefiles *directly* using `geopandas`.

Here is a map of NJ (sourced from [here](https://njogis-newjersey.opendata.arcgis.com/datasets/newjersey::county-boundaries-of-nj-hosted-3857/explore)). We load the shapefile using `geopandas` and then use `hvplot` to plot it

In [ ]:
# load the data directly
nj = gpd.read_file('data/NJ_Counties_3857.shp')
# All these files are shape file data
# geopandas to read shape files, gets needed data
# reads into geodataframe

nj

# because GeoDataFrames are ultimately DataFrames they too inherit the hvplot functionality 
nj.hvplot(
    color='POP2020',
    clabel='Population 2020',
    hover_cols=['COUNTY']
).opts(
    title='NJ Population by County - 2020',
    xlabel='Longitude (deg)',
    ylabel='Latitude (deg)',
    data_aspect=1, # ensure the data is not skewed
    show_grid=True,
    height=480,
    width=720
)

:Polygons   [x,y]   (POP2020,COUNTY)

Our shapefiles contained additional information pertaining to census data, and so we can use that data for coloring each of the resulting polygons. We can take these polygons and overlay them onto actual tilemaps with some simple tweaks.

In [ ]:
nj.hvplot(
    color='POP2020',
    alpha=0.75,
    clabel='Population 2020',
    hover_cols=['COUNTY'],
    tiles=True # take a map source and automatically overlay geometry on top of it
).opts(
    title='NJ Population by County - 2020',
    height=480,
    width=720
)

:Overlay
   .Tiles.I    :Tiles   [x,y]
   .Polygons.I :Polygons   [x,y]   (POP2020,COUNTY)

We can even define our own polygons and geometries to layer over a map. This could be used to show areas of interest or otherwise important features. All that we need to do is create polygons consisting of latitude/longitude vertices. Below we create a polygon by defining a list of longitude/latitude pairs, and then passing that wrapper in a another list to `gv.Polygons`. We need to wrap the shape in a list, as `gv.Polygons` expects to draw multiple polygons.

In [ ]:
triangle = [
    [-80.1918, 25.7617],
    [-66.1185, 18.4671],
    [-64.7505, 32.3078]
]
geo_triangle = gv.Polygons([triangle]).opts(color='red', alpha=0.5)
(esri_world * geo_triangle).opts(
    title='Bermuda Triangle',
    height=480,
    width=720
)

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]

In [ ]:
# dummy, simulated data
import numpy as np
glons, glats = np.meshgrid(
    np.linspace(-80, -63, 10),
    np.linspace(19, 33, 10)
)
u = 10 * (2 * np.cos(3 * np.deg2rad(glons) + 2 * np.deg2rad(glats + 21)) ** 2)
v = 25 * np.cos(6 * np.deg2rad(glons))
df = pd.DataFrame({
    'longitude': glons.flatten(),
    'latitude': glats.flatten(),
    'magnitude': 5.0,
    'angle': (np.pi / 2 - np.arctan2(v, u)).flatten() + np.pi/2
})
# end of simulated data

# create a vector field to simulate wind/air flow
air_field = gv.VectorField(df, kdims=['longitude', 'latitude'], vdims=['angle', 'magnitude']).opts(
    magnitude=hv.dim('magnitude')/10,
    color='white'
)
# vector field contains latitude, longitude, angle, magnitude
# arrows are used to display the flow (airflow or wind)
(esri_world * geo_triangle * air_field).opts(
    title='Bermuda Triangle - Air Flow',
    height=480,
    width=720
)

:Overlay
   .WMTS.I        :WMTS   [Longitude,Latitude]
   .Polygons.I    :Polygons   [Longitude,Latitude]
   .VectorField.I :VectorField   [longitude,latitude]   (angle,magnitude)

In [ ]:
dir(gv)

['Contours',
 'Cycle',
 'Dataset',
 'Dimension',
 'DynamicMap',
 'EdgePaths',
 'Feature',
 'FilledContours',
 'GeoviewsDeprecationWarning',
 'GeoviewsUserWarning',
 'Graph',
 'GridSpace',
 'HexTiles',
 'HoloMap',
 'Image',
 'Labels',
 'Layout',
 'LineContours',
 'NdLayout',
 'NdOverlay',
 'Nodes',
 'Overlay',
 'Palette',
 'Path',
 'Points',
 'Polygons',
 'QuadMesh',
 'RGB',
 'Rectangles',
 'Segments',
 'Shape',
 'Store',
 'Text',
 'Tiles',
 'TriMesh',
 'VectorField',
 'WMTS',
 'WindBarbs',
 '_Element',
 '__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__path__',
 '__spec__',
 '__version__',
 '_warnings',
 'annotate',
 'annotators',
 'copy_examples',
 'data',
 'dim',
 'element',
 'examples',
 'extension',
 'feature',
 'fetch_data',
 'from_xarray',
 'help',
 'links',
 'load_tiff',
 'models',
 'operation',
 'opts',
 'output',
 'param',
 'plotting',
 'project',
 'render',
 'renderer',
 'save',
 'streams',
 'tile_sources',
 'util']

## Exercise

We have a model of a drone that performs surveillence in a designated area; we want to plot the path of the drone as it is flying. We can get the position of the drone at a given point in time by calling the function `drone_model.fly` and passing in a time in seconds.

Use the [`Player`](https://panel.holoviz.org/reference/widgets/Player.html) widget from `panel` to simulate the playback of a drone flight from 0 seconds to 60 seconds. To do this you will need to create a dynamic map that overlays a `geoviews.Points` of the position on top of map tiles.

NOTE: if running this in a Codespace, this will be a bit *slow* as repeatedly and dynamically updating a map utilizing tiles is computationally intensive.

NOTE: standard features like `xlim` and `ylim` *will not work here*, and so to anchor the plot region we can use an invisible bounding box (rectangle) with a given location like so:

```python
center = (-75.12601884604852, 39.95066669151871)
bounding_box = gv.Rectangles([
    [center[0]-0.0015, center[1]-0.0015, center[0]+0.0015, center[1]+0.0015]
]).opts(color=None, line_color=None)
```

In [ ]:
# import our dummy model
import drone_model

# create a player
#
player = pn.widgets.Player(name='Player', start=0, end=60, interval=100)

# create the bounding box
#
center = (-75.12601884604852, 39.95066669151871)
bounding_box = gv.Rectangles([
    [center[0]-0.0015, center[1]-0.0015, center[0]+0.0015, center[1]+0.0015]
]).opts(color=None, line_color=None)

# create a world overlaid with the bounding_box, name it "field"
#
field = world * bounding_box

# create a function that depends on the player, mapping the player to an input named `time_s`
# and use that to call ther `drone.fly` function to get a point in space

path = []

@pn.depends(player = player)
def drone_simul(player):
    position = drone_model.fly(time_s = player)
    path.append(position)
    return field * gv.Path(path).opts(color = 'black') * gv.Points(position).opts(
        title = 'Sample Drone Simulation',
        size=10,
        color = 'red'
    ) 

# layout the player and a dynamic map in a column
pn.Column(
    player,
    hv.DynamicMap(drone_simul)
)


BokehModel(combine_events=True, render_bundle={'docs_json': {'c765a606-8903-4453-8a8b-52ec2e208ebc': {'version…

What are somes issues here? What could be better?